<a href="https://colab.research.google.com/github/VitorMagno/smtt/blob/main/smtt.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [1]:
import pandas as pd 
import numpy as np
import plotly.express as px


# Seção 1: limpeza e observação da tabela

In [2]:
#tabela origem
tabela_viagens = pd.read_csv('/content/drive/MyDrive/viagens.csv')
display(tabela_viagens.head())

Unnamed: 0  numero_viagem_da_linha_no_dia  ...  duracao_realizada  sentido_viagem
0           0                              1  ...               40.0             ida
1           1                              2  ...               40.0           volta
2           2                              3  ...               43.0             ida
3           3                              4  ...               44.0           volta
4           4                              5  ...               44.0             ida

[5 rows x 14 columns]

### Sugestão
  * A coluna *'hora_prevista'* e *'hora_realizada'* seria mais útil caso armazenasse apenas a hora e não data e hora, assim deixando o conteúdo das colunas apenas com números. Criando também uma outra coluna para registrar especificamente a data. Porém, da para manipular a string e eliminar linha por linha os caracteres especiais dessas colunas e depois converter para dados numéricos.

In [3]:
def valores_nulos(x): 
  """
  funcao que contabiliza os valores nulos 
  """
  return sum(x.isnull())

print ("valores nulos por coluna:")
# aplica a funcao que contabiliza os valores nulos e printa por coluna
print (tabela_viagens.apply(valores_nulos, axis=0))

print ("\nvalores nulos por linha:")
## aplica a funcao que contabiliza os valores nulos e printa por linha
print (tabela_viagens.apply(valores_nulos, axis=1).head())

valores nulos por coluna:
Unnamed: 0                          0
numero_viagem_da_linha_no_dia       0
ordem_veiculo_na_linha_no_dia       0
duracao_total_realizada          2630
nome_linha                          0
atendimento                         0
empresa                             0
numero_ordem_veiculo                0
numero_linha                        0
hora_prevista                       0
hora_realizada                   2174
duracao_prevista                    0
duracao_realizada                3533
sentido_viagem                      0
dtype: int64

valores nulos por linha:
0    0
1    0
2    0
3    0
4    0
dtype: int64


### Nota
* Vemos que há colunas com mais números nulos do que o esperado.  
  * Os números nulos das colunas em questão deveriam ser iguais, pois a falta de números em *'hora_realizada'* significa que a viagem não foi concluída, logo, também não haverá *'duracao_total_realizada'* e *'duracao_realizada'*.  

In [4]:
# filtrando colunas importantes e renomeando adequadamente
tabela_objetiva = tabela_viagens[['Unnamed: 0', 'nome_linha', 'atendimento', 'empresa', 'hora_realizada', 'duracao_prevista', 'duracao_realizada', 'sentido_viagem']]
tabela_objetiva.rename(columns={'Unnamed: 0':'total_viagens'},inplace=True)


/usr/local/lib/python3.6/dist-packages/pandas/core/frame.py:4308: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



### Checklist
- [x] fazer uma coluna nova que indique o estado da viagem (atrasada, adiantada, nao concluida ou concluida) 
- [x] fazer uma funcao que mude o estado da viagem 
- [x] fazer um for que aplique a funcao a toda as viagens
- [x] utilizando a biblioteca plotly.express, plotar graficos com a visao de cada coluna 

In [6]:
# cria uma nova coluna chamada estado_viagem
tabela_objetiva = tabela_objetiva.assign(estado_viagem='pontual')

def mudar_estado(i):
  """
  funcao que muda o estado_viagem, classificando como: adiantada, atrasada, pontual ou nao concluida
  """
  if isinstance(tabela_objetiva.loc[i, 'hora_realizada'], str):
    if tabela_objetiva.loc[i,'duracao_prevista'] > tabela_objetiva.loc[i,'duracao_realizada']:
      tabela_objetiva.loc[i, 'estado_viagem'] = 'adiantada'
    
    elif tabela_objetiva.loc[i, 'duracao_prevista'] == tabela_objetiva.loc[i, 'duracao_realizada']:
      tabela_objetiva.loc[i, 'estado_viagem'] = 'pontual'
    else:
      tabela_objetiva.loc[i, 'estado_viagem'] = 'atrasada'
  else:
    tabela_objetiva.loc[i, 'estado_viagem']= 'nao concluida'

#looping que aplica a funcao mudar_estado a tabela
for a in range(len(tabela_objetiva)):
  mudar_estado(a)


# Seção 2: Apresentação dos gráficos 

In [7]:
#looping que plota o grafico de todas as colunas em observacao ao estado da viagem
for coluna in tabela_objetiva:
  fig = px.histogram(tabela_objetiva, x=coluna, 
                      color='estado_viagem', 
                      color_discrete_map={
                      'pontual':'#7B68EE', 
                      'atrasada':'#CD5C5C', 
                      'nao concluida':'#8B0000'
    }
  )
  fig.show()

### Nota 
  * Após observar todos os gráficos, os que representaram indicadores relevantes são esses
    - estado_viagem
    - empresas
    - nome_linha
    - atendimento

# Seção 3: Observações
  * A empresa Auto Viaçao Veleiro LTDA tem sozinha metade das viagens não concluidas.  
  * A empresa Real Transportes Urbanos LTDA tem uma ótima relação entre viagens potuais e adiantadas contra viagens atrasadas.   
  * A linha de Alto de Ipioca é a que menos conclui viagens, quantitativamente.
  * A linha de Chã da Jaqueira / Ponta Verde é a que mais atrasa, quantitativamente.
  * Percentualmente a linha que mais atrasa é a Pontal / Ufal, mais de 95%.  

In [8]:
# plotando os graficos mais relevantes
fig_1 = px.histogram(tabela_objetiva, x='estado_viagem', 
                      color='estado_viagem', 
                      color_discrete_map={
                      'pontual':'#7B68EE', 
                      'atrasada':'#CD5C5C', 
                      'nao concluida':'#8B0000'})
fig_1.update_layout(
    title_text='Observação das viagens' 
)
fig_1.show()
fig_2 = px.histogram(tabela_objetiva, x='empresa', 
                      color='estado_viagem', 
                      color_discrete_map={
                      'pontual':'#7B68EE', 
                      'atrasada':'#CD5C5C', 
                      'nao concluida':'#8B0000'})
fig_2.update_layout(
    title_text='Observação do desempenho das empresas' 
)
fig_2.show()                    
fig_3 = px.histogram(tabela_objetiva, x='nome_linha', 
                      color='estado_viagem', 
                      color_discrete_map={
                      'pontual':'#7B68EE', 
                      'atrasada':'#CD5C5C', 
                      'nao concluida':'#8B0000'})
fig_3.update_layout(
    title_text='Observação das linhas'
)
fig_3.show()
fig_4 = px.histogram(tabela_objetiva, x='atendimento', 
                      color='estado_viagem', 
                      color_discrete_map={
                      'pontual':'#7B68EE', 
                      'atrasada':'#CD5C5C', 
                      'nao concluida':'#8B0000'})
fig_4.update_layout(
    title_text='Observação do antendimento'
) 
fig_4.show()                                        